In [15]:
import pandas as pd
import plotly.express as px
import json
import scipy
from IPython.display import display, clear_output

In [16]:
no_camera_case = r'imu_output_static-camera_20240403-211416.txt'
camera_case = r'imu_output_static-camera_20240403-212455.txt'

filedata = None

with open(no_camera_case, 'r') as f:
    filedata = f.readlines()
    
# Create a pandas dataframe
df = pd.DataFrame( columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-quaternion', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])
accumulator = []

# max_lines = 1000
# counter = 0
for line in filedata:
    try:
        # counter += 1
        #split by tab
        tokens = line.split('   ')
        timestamp = tokens[0]
        data = tokens[1]
        data = json.loads(data)
        quat = data['imu']['083A8DCCC7B5']['quaternion']
        #convert quat to euler
        quat = [quat['w'], quat['x'], quat['y'], quat['z']]
        euler = scipy.spatial.transform.Rotation.from_quat(quat).as_euler('xyz', degrees=True)
        accumulator.append([timestamp, quat, euler[0], euler[1], euler[2]])
        # if counter >= max_lines:
        #     break
    except Exception as e:
        print(e)
        print(line)
        continue
clear_output()
df = pd.concat([df, pd.DataFrame(accumulator, columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z'])], ignore_index=True)
display(df)

timestamp                                     imu-quaternion  \
0       457215.2918423  [0.984799862, -0.173478574, 0.013966521, 0.006...   
1       457215.2938007  [0.984823942, -0.173340052, 0.013964123, 0.006...   
2       457215.2960923  [0.984849095, -0.173196524, 0.013964517, 0.006...   
3       457215.2983194  [0.984888792, -0.172975928, 0.013961069, 0.006...   
4       457215.3005577  [0.984916866, -0.172812045, 0.013958298, 0.006...   
...                ...                                                ...   
264526  457814.0390739  [0.947568655, -0.021713465, -0.319023252, 0.00...   
264527  457814.0422553  [0.947571278, -0.021660596, -0.319019258, 0.00...   
264528  457814.0445419  [0.947573066, -0.021441787, -0.319017828, 0.00...   
264529  457814.0511614  [0.947573066, -0.021441787, -0.319017828, 0.00...   
264530  457814.0515666  [0.947574914, -0.021244287, -0.319023788, 0.00...   

        imu-euler-x  imu-euler-y  imu-euler-z camera-quaternion  \
0        179.520556    -1.709430   -19.973864               NaN   
1        179.519666    -1.709198   -19.957739               NaN   
2        179.519108    -1.709228   -19.941033               NaN   
3        179.517825    -1.708876   -19.915330               NaN   
4        179.516757    -1.708612   -19.896261               NaN   
...             ...          ...          ...               ...   
264526   178.112237    37.171448    -3.260227               NaN   
264527   178.157850    37.172231    -3.238502               NaN   
264528   178.177792    37.172880    -3.205354               NaN   
264529   178.177792    37.172880    -3.205354               NaN   
264530   178.174848    37.173685    -3.182482               NaN   

       camera-euler-x camera-euler-y camera-euler-z  
0                 NaN            NaN            NaN  
1                 NaN            NaN            NaN  
2                 NaN            NaN            NaN  
3                 NaN            NaN            NaN  
4                 NaN            NaN            NaN  
...               ...            ...            ...  
264526            NaN            NaN            NaN  
264527            NaN            NaN            NaN  
264528            NaN            NaN            NaN  
264529            NaN            NaN            NaN  
264530            NaN            NaN            NaN  

[264531 rows x 9 columns]

In [17]:
# subtract the average from each axis
df_mod = df.copy()
#convert timestamp from float to 
#time was timestamp = time.perf_counter()
df_mod['timestamp'] = pd.to_datetime(df_mod['timestamp'], unit='s')
#convert all values to float
df_mod['imu-euler-x'] = df_mod['imu-euler-x'].astype(float)
df_mod['imu-euler-y'] = df_mod['imu-euler-y'].astype(float)
df_mod['imu-euler-z'] = df_mod['imu-euler-z'].astype(float)


# get the average for each axis in euler
imu_euler_x_avg = df_mod['imu-euler-x'].mean()
imu_euler_y_avg = df_mod['imu-euler-y'].mean()
imu_euler_z_avg = df_mod['imu-euler-z'].mean()
df_mod['imu-euler-x'] = df_mod['imu-euler-x'] - imu_euler_x_avg
df_mod['imu-euler-y'] = df_mod['imu-euler-y'] - imu_euler_y_avg
df_mod['imu-euler-z'] = df_mod['imu-euler-z'] - imu_euler_z_avg
#decimate the data to 1/10
df_mod = df_mod[::10]
# plot 3 axis in the same plot
#convert timestamp to seconds subtract the first value
df_mod['timestamp'] = df_mod['timestamp'] - df_mod['timestamp'].iloc[0]
df_mod['timestamp'] = df_mod['timestamp'].dt.total_seconds()
fig = px.line(df_mod, x='timestamp', y=['imu-euler-x', 'imu-euler-y', 'imu-euler-z'])
fig.update_layout(title='IMU Euler angles (no camera correction)', xaxis_title='Time (s)', yaxis_title='Angle (deg)')

fig.show()
#save fig as html
plot_name = 'imu_euler_no_camera.html'
fig.write_html(plot_name)

In [18]:
#plot the histogram of each axis
for axis in ['imu-euler-x', 'imu-euler-y', 'imu-euler-z']:
    fig = px.histogram(df_mod, x=axis, nbins=100)
    fig.update_layout(
        title_text=f'{axis} histogram',
        xaxis_title='Degrees',
        yaxis_title='Count'
    )
    fig.show()
    plot_name = f'{axis}_histogram_no_camera.html'
    fig.write_html(plot_name)

In [19]:


filedata = None

with open(camera_case, 'r') as f:
    filedata = f.readlines()
    
# Create a pandas dataframe
df = pd.DataFrame( columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-quaternion', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])
accumulator = []

# max_lines = 10
# counter = 0
for line in filedata:
    try:
        #split by tab
        tokens = line.split('   ')
        timestamp = tokens[0]
        data = tokens[1]
        data = json.loads(data)
        if 'camera' in data and data['camera'] is not None:
            tokens = line.split('   ')
            timestamp = tokens[0]
            data = tokens[1]
            data = json.loads(data)
            imuquat = data['imu']['083A8DCCC7B5']['quaternion']
            #convert quat to euler
            imuquat = [imuquat['w'], imuquat['x'], imuquat['y'], imuquat['z']]
            #get camera data
            camquat = data['camera']['2']['quaternion']
            #convert quat to euler
            camquat = [camquat['w'], camquat['x'], camquat['y'], camquat['z']]
            imu_euler = scipy.spatial.transform.Rotation.from_quat(imuquat).as_euler('xyz', degrees=True)
            cam_euler = scipy.spatial.transform.Rotation.from_quat(camquat).as_euler('xyz', degrees=True)
            accumulator.append([timestamp, imuquat, imu_euler[0], imu_euler[1], imu_euler[2], camquat, cam_euler[0], cam_euler[1], cam_euler[2]])
            # counter += 1
            # if counter >= max_lines:
            #     break
    except Exception as e:
        print(f"Error: {e}")
        break
clear_output()
df = pd.concat([df, pd.DataFrame(accumulator, columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-quaternion', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])], ignore_index=True)
display(df)

timestamp                                     imu-quaternion  \
0      457852.6244656  [0.940566301, -0.020957917, -0.339167207, 0.00...   
1      457852.6257622  [0.940565705, -0.021087795, -0.339164704, 0.00...   
2      457852.6284367  [0.940558016, -0.021107733, -0.33916831, 0.006...   
3      457852.6291775  [0.940560281, -0.020916462, -0.339168519, 0.00...   
4      457852.6294903  [0.940564752, -0.020721257, -0.339167774, 0.00...   
...               ...                                                ...   
13332  457889.7019546  [0.997831762, -0.017243803, -0.063885644, 0.01...   
13333    457889.70394  [0.997828722, -0.017205834, -0.063918389, 0.01...   
13334  457889.7085414  [0.997826338, -0.017126054, -0.063960508, 0.01...   
13335  457889.7102886  [0.997825742, -0.017017245, -0.064004958, 0.01...   
13336   457889.714795  [0.997825205, -0.016956031, -0.06405735, 0.010...   

       imu-euler-x  imu-euler-y  imu-euler-z  \
0       178.102711    39.617220    -3.236376   
1       178.107014    39.616885    -3.250636   
2       178.074249    39.616672    -3.264886   
3       178.073119    39.616879    -3.241999   
4       178.085071    39.617247    -3.213917   
...            ...          ...          ...   
13332   178.597108     7.301528    -2.069606   
13333   178.593496     7.305281    -2.065529   
13334   178.592179     7.310202    -2.056520   
13335   178.601224     7.315609    -2.043517   
13336   178.609146     7.321835    -2.036060   

                                       camera-quaternion  camera-euler-x  \
0      [0.9967294609516282, 0.01500674532234241, -0.0...     -179.451225   
1      [0.9967294609516282, 0.01500674532234241, -0.0...     -179.451225   
2      [0.9967294609516282, 0.01500674532234241, -0.0...     -179.451225   
3      [0.9967294609516282, 0.01500674532234241, -0.0...     -179.451225   
4      [0.9967294609516282, 0.01500674532234241, -0.0...     -179.451225   
...                                                  ...             ...   
13332  [0.9972510811069323, 0.02338069794160218, -0.0...     -179.420516   
13333  [0.9972510811069323, 0.02338069794160218, -0.0...     -179.420516   
13334  [0.9972510811069323, 0.02338069794160218, -0.0...     -179.420516   
13335  [0.9972510811069323, 0.02338069794160218, -0.0...     -179.420516   
13336  [0.9973815602974728, 0.021860167369157753, -0....     -179.380713   

       camera-euler-y  camera-euler-z  
0            9.092343        1.768793  
1            9.092343        1.768793  
2            9.092343        1.768793  
3            9.092343        1.768793  
4            9.092343        1.768793  
...               ...             ...  
13332        8.042979        2.726864  
13333        8.042979        2.726864  
13334        8.042979        2.726864  
13335        8.042979        2.726864  
13336        7.881601        2.553827  

[13337 rows x 9 columns]

In [20]:
# subtract the average from each axis
df_mod = df.copy()
#ignore the first 1000 samples
df_mod['timestamp'] = pd.to_datetime(df_mod['timestamp'], unit='s')
#convert all values to float
df_mod['imu-euler-x'] = df_mod['imu-euler-x'].astype(float)
df_mod['imu-euler-y'] = df_mod['imu-euler-y'].astype(float)
df_mod['imu-euler-z'] = df_mod['imu-euler-z'].astype(float)
df_mod['camera-euler-x'] = df_mod['camera-euler-x'].astype(float)
df_mod['camera-euler-y'] = df_mod['camera-euler-y'].astype(float)
df_mod['camera-euler-z'] = df_mod['camera-euler-z'].astype(float)

#decimate the data to 1/10
df_mod = df_mod[::10]
df_mod['timestamp'] = df_mod['timestamp'] - df_mod['timestamp'].iloc[0]
df_mod['timestamp'] = df_mod['timestamp'].dt.total_seconds()
# plot 3 axis in the same plot
fig = px.line(df_mod, x='timestamp', y=['imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])
fig.update_layout(title='IMU Euler angles Camera Correction', xaxis_title='Time (s)', yaxis_title='Angle (deg)')
fig.show()
#save fig as html
plot_name = 'imu_euler_camera.html'
fig.write_html(plot_name)

In [21]:
#plot the histogram of each axis
for axis in ['imu-euler-x', 'imu-euler-y', 'imu-euler-z']:
    fig = px.histogram(df_mod, x=axis, nbins=100)
    fig.update_layout(
        title_text=f'{axis} histogram',
        xaxis_title='Degrees',
        yaxis_title='Count'
    )
    fig.show()
    plot_name = f'{axis}_histogram_camera.html'
    fig.write_html(plot_name)

In [22]:
latency_data = r'latency_output_static-camera_20240403-215041.txt'

filedata = None
with open(latency_data, 'r') as f:
    filedata = f.readlines()

df_imu_latency = pd.DataFrame( columns=['timestamp'])    
df_camera_latency = pd.DataFrame( columns=['timestamp'])
df_camera_accumulator = []
df_imu_accumulator = []
for line in filedata:
    try:
        #split by tab
        tokens = line.split('   ')
        timestamp = tokens[0]
        data = tokens[1]
        timestamp = pd.to_datetime(float(timestamp), unit='s')
        if 'camera' in data:
            df_camera_accumulator.append([timestamp])
        elif 'imu' in data:
            df_imu_accumulator.append([timestamp])
    except Exception as e:
        print(f"Error: {e}")
        continue

df_imu_latency = pd.concat([df_imu_latency, pd.DataFrame(df_imu_accumulator, columns=['timestamp'])], ignore_index=True)
df_camera_latency = pd.concat([df_camera_latency, pd.DataFrame(df_camera_accumulator, columns=['timestamp'])], ignore_index=True)
display(df_imu_latency)
display(df_camera_latency)

# get the difference between the two dataframes
df_camera_latency['camera_latency'] = df_camera_latency['timestamp'].diff()
df_imu_latency['imu_latency'] = df_imu_latency['timestamp'].diff()
#mean of the latency
imu_latency_mean = df_imu_latency['imu_latency'].mean()
camera_latency_mean = df_camera_latency['camera_latency'].mean()
#biggest latency
imu_latency_max = df_imu_latency['imu_latency'].max()
camera_latency_max = df_camera_latency['camera_latency'].max()
#convert to df datetime to float
imu_latency_mean = imu_latency_mean.total_seconds()
camera_latency_mean = camera_latency_mean.total_seconds()
imu_latency_max = imu_latency_max.total_seconds()
camera_latency_max = camera_latency_max.total_seconds()
#conver to ms
imu_latency_mean = imu_latency_mean * 1000
camera_latency_mean = camera_latency_mean * 1000
imu_latency_max = imu_latency_max * 1000
camera_latency_max = camera_latency_max * 1000
clear_output()
print(f"imu latency mean: {imu_latency_mean} ms")
print(f"camera latency mean: {camera_latency_mean} ms")
print(f"imu latency max: {imu_latency_max} ms")
print(f"camera latency max: {camera_latency_max} ms")
#convert latency to seconds
df_imu_latency['imu_latency'] = df_imu_latency['imu_latency'].dt.total_seconds()
df_camera_latency['camera_latency'] = df_camera_latency['camera_latency'].dt.total_seconds()
#convert to ms
df_imu_latency['imu_latency'] = df_imu_latency['imu_latency'] * 1000
df_camera_latency['camera_latency'] = df_camera_latency['camera_latency'] * 1000
#plot the histogram of each axis
# IMU Latency Histogram
fig_imu = px.histogram(df_imu_latency, x='imu_latency', nbins=100)
fig_imu.update_layout(
    title_text='IMU Latency Distribution',
    xaxis_title='Latency (ms)',
    yaxis_title='Count'
)
fig_imu.show()

# Save the IMU latency histogram plot
plot_name_imu = 'imu_latency_histogram.html'
fig_imu.write_html(plot_name_imu)


plot_name = 'imu_latency_histogram.html'
fig.write_html(plot_name)

fig_camera = px.histogram(df_camera_latency, x='camera_latency', nbins=100)
fig_camera.update_layout(
    title_text='Camera Latency Distribution',
    xaxis_title='Latency (ms)',
    yaxis_title='Count'
)
fig_camera.show()
#xaxis_title="Latency (ms)",
fig.update_xaxes(title_text='Latency (ms)')


plot_name = 'camera_latency_histogram.html'
fig.write_html(plot_name)


imu latency mean: 2.561 ms
camera latency mean: 33.633 ms
imu latency max: 24.662 ms
camera latency max: 86.887 ms
